# Explore here

In [33]:
import pandas as pd
import json
import sqlite3

df_movies = pd.read_csv("https://raw.githubusercontent.com/4GeeksAcademy/k-nearest-neighbors-project-tutorial/main/tmdb_5000_movies.csv")
df_credits = pd.read_csv("https://raw.githubusercontent.com/4GeeksAcademy/k-nearest-neighbors-project-tutorial/main/tmdb_5000_credits.csv")

pd.set_option('display.max_columns', None)

In [34]:
for col in df_movies.columns:
    print(col)

budget
genres
homepage
id
keywords
original_language
original_title
overview
popularity
production_companies
production_countries
release_date
revenue
runtime
spoken_languages
status
tagline
title
vote_average
vote_count


In [35]:
for col in df_credits.columns:
    print(col)

movie_id
title
cast
crew


In [36]:
df_credits.drop(['title'], axis=1, inplace=True)

In [37]:
df_credits.shape

(4803, 3)

In [38]:
df_movies.shape

(4803, 20)

In [39]:
conn = sqlite3.connect(':memory:')

# Guardar los DataFrames como tablas en la base de datos SQLite
df_movies.to_sql('movies', conn, index=False)
df_credits.to_sql('credits', conn, index=False)

# Ejecutar una consulta SQL para combinar los datos de ambas tablas
query = '''
        SELECT *
        FROM movies
        INNER JOIN credits ON movies.id = credits.movie_id
        '''

# Ejecutar la consulta y obtener el resultado como un DataFrame
df_combined = pd.read_sql(query, conn)

In [40]:
df_combined.shape

(4803, 23)

In [41]:
df_combined.head(2)

budget  \
0  237000000   
1  300000000   

                                                                                                                                   genres  \
0  [{"id": 28, "name": "Action"}, {"id": 12, "name": "Adventure"}, {"id": 14, "name": "Fantasy"}, {"id": 878, "name": "Science Fiction"}]   
1                                          [{"id": 12, "name": "Adventure"}, {"id": 14, "name": "Fantasy"}, {"id": 28, "name": "Action"}]   

                                       homepage     id  \
0                   http://www.avatarmovie.com/  19995   
1  http://disney.go.com/disneypictures/pirates/    285   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          keywords  \
0  [{"id": 1463, "name": "culture clash"}, {"id": 2964, "name": "future"}, {"id": 3386, "name": "space war"}, {"id": 3388, "name": "space colony"}, {"id": 3679, "name": "society"}, {"id": 3801, "name": "space travel"}, {"id": 9685, "name": "futuristic"}, {"id": 9840, "name": "romance"}, {"id": 9882, "name": "space"}, {"id": 9951, "name": "alien"}, {"id": 10148, "name": "tribe"}, {"id": 10158, "name": "alien planet"}, {"id": 10987, "name": "cgi"}, {"id": 11399, "name": "marine"}, {"id": 13065, "name": "soldier"}, {"id": 14643, "name": "battle"}, {"id": 14720, "name": "love affair"}, {"id": 165431, "name": "anti war"}, {"id": 193554, "name": "power relations"}, {"id": 206690, "name": "mind and soul"}, {"id": 209714, "name": "3d"}]   
1                                                                                                                                                   [{"id": 270, "name": "ocean"}, {"id": 726, "name": "drug abuse"}, {"id": 911, "name": "exotic island"}, {"id": 1319, "name": "east india trading company"}, {"id": 2038, "name": "love of one's life"}, {"id": 2052, "name": "traitor"}, {"id": 2580, "name": "shipwreck"}, {"id": 2660, "name": "strong woman"}, {"id": 3799, "name": "ship"}, {"id": 5740, "name": "alliance"}, {"id": 5941, "name": "calypso"}, {"id": 6155, "name": "afterlife"}, {"id": 6211, "name": "fighter"}, {"id": 12988, "name": "pirate"}, {"id": 157186, "name": "swashbuckler"}, {"id": 179430, "name": "aftercreditsstinger"}]   

  original_language                            original_title  \
0                en                                    Avatar   
1                en  Pirates of the Caribbean: At World's End   

                                                                                                                                                                           overview  \
0   In the 22nd century, a paraplegic Marine is dispatched to the moon Pandora on a unique mission, but becomes torn between following orders and protecting an alien civilization.   
1  Captain Barbossa, long believed to be dead, has come back to life and is headed to the edge of the Earth with Will Turner and Elizabeth Swann. But nothing is quite as it seems.   

   popularity  \
0  150.437577   
1  139.082615   

                                                                                                                                                                                          production_companies  \
0  [{"name": "Ingenious Film Partners", "id": 289}, {"name": "Twentieth Century Fox Film Corporation", "id": 306}, {"name":

In [42]:
df_combined.drop(['budget', 'homepage', 'original_language', 'tagline', 'original_title', 'popularity', 'production_companies', 'production_countries', 'release_date', 'revenue', 'runtime', 'spoken_languages', 'status', 'vote_average', 'vote_count', 'id'], axis=1, inplace=True)

In [43]:
def extraer_nombres(lista_diccionarios, limit=None):
    try:
        # Convertir la cadena JSON a una lista de diccionarios
        lista_diccionarios = json.loads(lista_diccionarios)
        # Si no se especifica un límite, extraer todos los nombres
        if limit is None:
            nombres = [item['name'] for item in lista_diccionarios]
        else:
            # Si se especifica un límite, extraer solo los primeros 'limit' nombres
            nombres = [item['name'] for item in lista_diccionarios[:limit]]
        return nombres
    except (json.JSONDecodeError, KeyError):
        # En caso de error o si la clave 'name' no está presente, retornar una lista vacía
        return []
    
# Aplicar la función a todas las columnas, excepto a 'cast'
columnas_json = ['genres', 'keywords']
for columna in columnas_json:
    df_combined[columna] = df_combined[columna].apply(extraer_nombres)

# Aplicar la función a la columna 'cast', limitando a los primeros tres nombres
df_combined['cast'] = df_combined['cast'].apply(extraer_nombres, limit=3)

In [44]:
def extract_director_name(crew_json):
    try:
        # Convertir la cadena JSON a una lista de diccionarios
        crew_list = json.loads(crew_json)
        
        # Buscar el diccionario con 'job' igual a 'Director'
        director_dict = next((item for item in crew_list if item['job'] == 'Director'), None)
        
        # Si se encuentra el diccionario del director, devolver su nombre, de lo contrario devolver None
        if director_dict:
            return director_dict['name']
        else:
            return None
    except (json.JSONDecodeError, KeyError):
        # En caso de error o si la columna no está en formato JSON, retornar None
        return None
    
df_combined['crew'] = df_combined['crew'].apply(lambda x: [extract_director_name(x)])

In [45]:
df_combined.shape

(4803, 7)

In [46]:
# Convertir el contenido de la columna 'overview' en listas de palabras
df_combined['overview'] = df_combined['overview'].astype(str)
df_combined['overview'] = df_combined['overview'].apply(lambda x: x.split())

In [47]:
pd.set_option('display.max_colwidth', None)

In [48]:
def reemplazar_nulos_con_listas_vacias(df, columnas):
    for columna in columnas:
        df_combined['genres'] = df_combined['genres'].apply(lambda x: [] if pd.isnull(x) else x)
        df_combined['cast'] = df_combined['cast'].apply(lambda x: [] if pd.isnull(x) else x)
        df_combined['crew'] = df_combined['crew'].apply(lambda x: [] if pd.isnull(x) else x)
        df_combined['overview'] = df_combined['overview'].apply(lambda x: [] if pd.isnull(x) else x)
    return df_combined

In [49]:
def eliminar_espacios(texto):
    if texto is not None:
        # Si el texto es una cadena de caracteres, eliminar los espacios entre palabras
        if isinstance(texto, str):
            return ''.join(texto.split())
        # Si el texto es una lista, eliminar los espacios entre palabras en cada elemento
        elif isinstance(texto, list):
            return [''.join(palabra.split()) if isinstance(palabra, str) else palabra for palabra in texto]
    # Si el texto es None, devolver None sin cambios
    return texto


df_combined['genres'] = df_combined['genres'].apply(eliminar_espacios)
df_combined['cast'] = df_combined['cast'].apply(eliminar_espacios)
df_combined['crew'] = df_combined['crew'].apply(eliminar_espacios)
df_combined['keywords'] = df_combined['keywords'].apply(eliminar_espacios)


In [50]:
df_combined.head(2)

genres  \
0  [Action, Adventure, Fantasy, ScienceFiction]   
1                  [Adventure, Fantasy, Action]   

                                                                                                                                                                                                         keywords  \
0  [cultureclash, future, spacewar, spacecolony, society, spacetravel, futuristic, romance, space, alien, tribe, alienplanet, cgi, marine, soldier, battle, loveaffair, antiwar, powerrelations, mindandsoul, 3d]   
1             [ocean, drugabuse, exoticisland, eastindiatradingcompany, loveofone'slife, traitor, shipwreck, strongwoman, ship, alliance, calypso, afterlife, fighter, pirate, swashbuckler, aftercreditsstinger]   

                                                                                                                                                                                                              overview  \
0         [In, the, 22nd, century,, a, paraplegic, Marine, is, dispatched, to, the, moon, Pandora, on, a, unique, mission,, but, becomes, torn, between, following, orders, and, protecting, an, alien, civilization.]   
1  [Captain, Barbossa,, long, believed, to, be, dead,, has, come, back, to, life, and, is, headed, to, the, edge, of, the, Earth, with, Will, Turner, and, Elizabeth, Swann., But, nothing, is, quite, as, it, seems.]   

                                      title  movie_id  \
0                                    Avatar     19995   
1  Pirates of the Caribbean: At World's End       285   

                                            cast             crew  
0  [SamWorthington, ZoeSaldana, SigourneyWeaver]   [JamesCameron]  
1     [JohnnyDepp, OrlandoBloom, KeiraKnightley]  [GoreVerbinski]

In [51]:
df_combined.shape

(4803, 7)

In [52]:
df_combined['tags'] = df_combined.apply(lambda row: ' '.join(row.astype(str)), axis=1)
df_combined['tags'] = df_combined['tags'].str.replace(r"[\[\]\']", '', regex=True)
df_combined['tags'] = df_combined['tags'].str.replace(',', ' ')


In [53]:
import re

# Función para limpiar los signos de puntuación
def limpiar_signos(texto):
    # Utilizar una expresión regular para eliminar los signos de puntuación
    texto_limpio = re.sub(r'[^\w\s]', '', texto)
    return texto_limpio

df_combined['tags'] = df_combined['tags'].apply(limpiar_signos)
df_combined.head(3)

genres  \
0  [Action, Adventure, Fantasy, ScienceFiction]   
1                  [Adventure, Fantasy, Action]   
2                    [Action, Adventure, Crime]   

                                                                                                                                                                                                         keywords  \
0  [cultureclash, future, spacewar, spacecolony, society, spacetravel, futuristic, romance, space, alien, tribe, alienplanet, cgi, marine, soldier, battle, loveaffair, antiwar, powerrelations, mindandsoul, 3d]   
1             [ocean, drugabuse, exoticisland, eastindiatradingcompany, loveofone'slife, traitor, shipwreck, strongwoman, ship, alliance, calypso, afterlife, fighter, pirate, swashbuckler, aftercreditsstinger]   
2                                                                                                                              [spy, basedonnovel, secretagent, sequel, mi6, britishsecretservice, unitedkingdom]   

                                                                                                                                                                                                                                                                                     overview  \
0                                                                                [In, the, 22nd, century,, a, paraplegic, Marine, is, dispatched, to, the, moon, Pandora, on, a, unique, mission,, but, becomes, torn, between, following, orders, and, protecting, an, alien, civilization.]   
1                                                                         [Captain, Barbossa,, long, believed, to, be, dead,, has, come, back, to, life, and, is, headed, to, the, edge, of, the, Earth, with, Will, Turner, and, Elizabeth, Swann., But, nothing, is, quite, as, it, seems.]   
2  [A, cryptic, message, from, Bond’s, past, sends, him, on, a, trail, to, uncover, a, sinister, organization., While, M, battles, political, forces, to, keep, the, secret, service, alive,, Bond, peels, back, the, layers, of, deceit, to, reveal, the, terrible, truth, behind, SPECTRE.]   

                                      title  movie_id  \
0                                    Avatar     19995   
1  Pirates of the Caribbean: At World's End       285   
2                                   Spectre    206647   

                                            cast             crew  \
0  [SamWorthington, ZoeSaldana, SigourneyWeaver]   [JamesCameron]   
1     [JohnnyDepp, OrlandoBloom, KeiraKnightley]  [GoreVerbinski]   
2      [DanielCraig, ChristophWaltz, LéaSeydoux]      [SamMendes]   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            tags  
0        Action  Adventure  Fantasy  ScienceFiction cultureclash  future  spacewar  spacecolony  society  spacetravel  futuristic  romance  space  alien  tribe  alienplanet  cgi  marine  soldier  battle  loveaffair  antiwar  powerrelations  mindandsoul  3d In  the  22nd  century   a  paraplegic  Marine  is  dispatched  to  the  moon  Pandora  on  a  unique  mission   but  becomes  torn  between  following  orders  and  protecting  an  alien  civilization Avatar 19995 SamWorthington  ZoeSaldana  SigourneyWeaver JamesCameron  
1  Adventure  Fantasy  Action ocean  drugabuse  exoticisland  eastindiatradingcompany  loveofoneslife  traitor  shipwreck  strongwoman  ship  alliance  calypso  afterlife  fighter  pirate  swashbuckler  aftercreditsstinger Captain  Barbossa   long  believed 

In [54]:
df_combined.shape

(4803, 8)

In [55]:
df_combined['tags'][0]

'Action  Adventure  Fantasy  ScienceFiction cultureclash  future  spacewar  spacecolony  society  spacetravel  futuristic  romance  space  alien  tribe  alienplanet  cgi  marine  soldier  battle  loveaffair  antiwar  powerrelations  mindandsoul  3d In  the  22nd  century   a  paraplegic  Marine  is  dispatched  to  the  moon  Pandora  on  a  unique  mission   but  becomes  torn  between  following  orders  and  protecting  an  alien  civilization Avatar 19995 SamWorthington  ZoeSaldana  SigourneyWeaver JamesCameron'

In [56]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Vectorización de texto
vectorizer = TfidfVectorizer()
vectors = vectorizer.fit_transform(df_combined['tags'])

In [57]:
from sklearn.metrics.pairwise import cosine_similarity

# Cálculo de similitud coseno
similarity = cosine_similarity(vectors)

In [58]:
import numpy as np

# Encuentra los índices de los vecinos más cercanos para cada instancia
k = 5  # Número de vecinos más cercanos
nearest_neighbors = np.argpartition(similarity, -k, axis=1)[:, -k:]

In [59]:
# Ejemplo de predicción para la primera instancia de prueba
indice_instancia_prueba = 0
vecinos_mas_cercanos = nearest_neighbors[indice_instancia_prueba]

# Obtén las etiquetas asociadas con los vecinos más cercanos
etiquetas_vecinos = df_combined['tags'].iloc[vecinos_mas_cercanos].tolist()

# Calcula la etiqueta más común entre los vecinos más cercanos
from collections import Counter
etiqueta_predicha = Counter(etiquetas_vecinos).most_common(1)[0][0]


In [60]:
def recommend(movie):
    # Encuentra el índice de la película en tu DataFrame
    movie_index = df_combined[df_combined["title"] == movie].index[0]
    
    # Calcula las distancias de similitud entre la película de entrada y todas las demás
    distances = similarity[movie_index]
    
    # Encuentra los índices de las películas más similares (excepto la película de entrada)
    movie_indices = sorted(range(len(distances)), key=lambda i: distances[i], reverse=True)[1:6]
    
    # Imprime los títulos de las películas más similares
    for index in movie_indices:
        print(df_combined.iloc[index]["title"])

In [61]:
recommend('Avatar')

Aliens
The Marine
Apollo 18
Star Trek Into Darkness
Titan A.E.


In [62]:
tfidf_df = pd.DataFrame(vectors.toarray(), columns=vectorizer.get_feature_names_out())
tfidf_df.head(2)

00  000  000foot  000yearold  007   10  100  1000  10003  100042  10008  \
0  0.0  0.0      0.0         0.0  0.0  0.0  0.0   0.0    0.0     0.0    0.0   
1  0.0  0.0      0.0         0.0  0.0  0.0  0.0   0.0    0.0     0.0    0.0   

   10012  10013  10014  10016  10017  10022  10024  100241  10025  10027  \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0     0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0     0.0    0.0    0.0   

   100275  10028  10029  10030  10034  10040  100402  10045  10047  10048  \
0     0.0    0.0    0.0    0.0    0.0    0.0     0.0    0.0    0.0    0.0   
1     0.0    0.0    0.0    0.0    0.0    0.0     0.0    0.0    0.0    0.0   

   10050  10052  10053  10054  10060  10061  10065  10066  10067  10068  \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   10069  10070  10071  10072  10073  10074  10075  10077  10090  10092  \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   10096  100975  10105  10115  10117  101173  101179  101267  101299  10131  \
0    0.0     0.0    0.0    0.0    0.0     0.0     0.0     0.0     0.0    0.0   
1    0.0     0.0    0.0    0.0    0.0     0.0     0.0     0.0     0.0    0.0   

   10132  10133  10135  10136  10137  10138  10139  10140  10147  10152  \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   10153  10154  10156  10159  10160  10162  10163  10167  10179  1018  10183  \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   0.0    0.0   

   10184  10185  10186  10187  10188  10189  10191  10192  10193  10195  \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   10196  10197  10198  10199  101yearold  102  10200  10201  10202  10204  \
0    0.0    0.0    0.0    0.0         0.0  0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0         0.0  0.0    0.0    0.0    0.0    0.0   

   10207  10208  10212  10214  10215  10217  10218  10219  10220  10223  \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   10225  10226  10229  102362  10238  102382  1024  10246  10253  102651  \
0    0.0    0.0    0.0     0.0    0.0     0.0   0.0    0.0    0.0     0.0   
1    0.0    0.0    0.0     0.0    0.0     0.0   0.0    0.0    0.0     0.0   

   10269  10279  10280  10281  10283  102840  10285  10288  102899  103  \
0    0.0    0.0    0.0    0.0    0.0     0.0    0.0    0.0     0.0  0.0   
1    0.0    0.0    0.0    0.0    0.0     0.0    0.0    0.0     0.0  0.0   

   10306  10307  10312  10313  10314  10315  10316  10317  10320  10327  \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   10329  10330  10331  103328  10333  10336  103370  10339  10350  10353  \
0    0.0    0.0    0.0     0.0    0.0    0.0     0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0     0.0    0.0    0.0     0.0    0.0    0.0    0.0   

   10357  10358  10362  103620  10364  10366  103663  10368  103731  10375  \
0    0.0    0.0    0.0     0.0    0.0    0.0     0.0    0.0     0.0    0.0   
1    0.0    0.0    0.0     0.0    0.0    0.0     0.0    0.0     0.0    0.0   

   10377  10383  10384  10385  10386  10388  10390  103903  10391  10393  \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0     0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0     0.0    0.0    0.0   

   10395  10397  10398  104  10400  10402  10410  10413  10414  10416  1042

In [63]:
tfidf_df.shape

(4803, 43358)